<a href="https://colab.research.google.com/github/shshahul/Zen_Project2/blob/main/Phonepe_Pulse_DataVisualisation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#  Extract data from the Phonepe pulse Github repository through scripting and clone it..

In [1]:
#cloning the repository from git hub

! git clone "https://github.com/PhonePe/pulse.git"

Cloning into 'pulse'...
remote: Enumerating objects: 7975, done.
remote: Counting objects: 100% (7975/7975), done.
remote: Compressing objects: 100% (6637/6637), done.
remote: Total 7975 (delta 2465), reused 6527 (delta 1031), pack-reused 0
Receiving objects: 100% (7975/7975), 2.11 MiB | 3.96 MiB/s, done.
Resolving deltas: 100% (2465/2465), done.


# Transform the data into a suitable format and perform any necessary cleaning and pre-processing steps.

In [3]:
#After created the clone of GIT-HUB repository then,
#import libraries for the program

import pandas as pd
import json
import os

#This is to direct the path to get the data as states

path1="/content/pulse/data/aggregated/transaction/country/india/state/"
Agg_state_list=os.listdir(path1)
Agg_state_list
#Agg_state_list--> to get the list of states in India

#<------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------>#

#This is to extract the data's to create a dataframe

clm={'State':[], 'Year':[],'Quater':[],'Transacion_type':[], 'Transacion_count':[], 'Transacion_amount':[]}
for i in Agg_state_list:
    p_i=path1+i+"/"
    Agg_yr=os.listdir(p_i)    
    for j in Agg_yr:
        p_j=p_i+j+"/"
        Agg_yr_list=os.listdir(p_j)        
        for k in Agg_yr_list:
            p_k=p_j+k
            Data=open(p_k,'r')
            D=json.load(Data)
            for z in D['data']['transactionData']:
              Name=z['name']
              count=z['paymentInstruments'][0]['count']
              amount=z['paymentInstruments'][0]['amount']
              clm['Transacion_type'].append(Name)
              clm['Transacion_count'].append(count)
              clm['Transacion_amount'].append(amount)
              clm['State'].append(i)
              clm['Year'].append(j)
              clm['Quater'].append(int(k.strip('.json')))
#Succesfully created a dataframe
pd.DataFrame(clm)
dfAg = pd.DataFrame(clm)


In [9]:
# insert the dataframe into a sqlite database
import sqlite3
con = sqlite3.connect('pulse.db')
c = con.cursor()

In [10]:
#Create a table in database
c.execute('''CREATE TABLE IF NOT EXISTS transaction_data(
            State TEXT,
            Year TEXT,
            Quater TEXT,
            Transacion_type TEXT,
            Transacion_count TEXT,
            Transacion_amount TEXT
            )''')


In [11]:
#insert the All data into the table
c.executemany('INSERT INTO transaction_data VALUES(?,?,?,?,?,?)',
              zip(clm['State'], clm['Year'],clm['Quater'],clm['Transacion_type'], clm['Transacion_count'], clm['Transacion_amount']))


In [ ]:
#show the data in the table
x=c.execute("SELECT * FROM transaction_data")
x=c.fetchall()
for row in x:
    print(row)

In [ ]:
#fetch the data from the table where the state is Tamil Nadu and year is 2018 and quater is 1 and transaction type is Recharge and bill payments

d=c.execute("SELECT * FROM transaction_data WHERE State='andhra-pradesh' AND Year='2018' AND Quater='1' AND Transacion_type='Recharge & bill payments' AND Transacion_amount>0")
d=c.fetchall()
for row in d:
  print(row)

In [14]:
# Commit changes and close connection
con.commit()
con.close()

In [ ]:
# #Connect to the database by excuting the following 
# conn = sqlite3.connect('transaction_data.db')
# c = conn.cursor()
# #Execute the SELECT statement
# c.execute("SELECT * FROM transaction_data")

# # Fetch all the rows in the result set
# rows = c.fetchall()

# # Loop through each row and print the data
# for row in rows:
#     print(row)

# # Close the cursor and the connection
# c.close()
# conn.close()

In [ ]:
path2 = "/content/pulse/data/aggregated/user/country/india/state/"
Agg_transc_user_list = os.listdir(path2)

#extracting the data from Aggregate---->Transaction--->user--->state to create the dataframe

clm = clm={"No of Registered User":[],"AppOpens":[],"Brand":[],"count":[],"Percentage":[],'State':[], 'Year':[], "Quarter":[]}

for i in Agg_transc_user_list:
  p_i = path2 + i +"/"
  Agg_year = os.listdir(p_i)
  for j in Agg_year:
    p_j = p_i + j + "/"
    Agg_year_list = os.listdir(p_j)
    for k in Agg_year_list:
      p_k = p_j + k
      with open(p_k,'r') as f:
        data = json.load(f)        
        clm['No of Registered User'].append(data['data']['aggregated']['registeredUsers'])
        clm['AppOpens'].append(data['data']['aggregated']['appOpens'])
        clm['Percentage'].append(data['data']['usersByDevice'][0]['percentage'])
        #clm['Brand'].append(data['data']['usersByDevice'])
        clm['State'].append(i)
        clm['Year'].append(j)
        clm['Quarter'].append(int(k.strip('.json')))

        for userdevice in data['data']['usersByDevice'][0]['brand']:
          clm['Brand'].append(userdevice)




          


In [15]:
# In this path extracting json data in to dataframe map-->transaction-->hover-->country-->india-->state
path3 = "/content/pulse/data/map/transaction/hover/country/india/state/"
map_state_list = os.listdir(path3)

# This is to extract the data's to create a dataframe
clm = {'State': [], 'district':[],'Year': [], 'Quarter': [], 'Metric_type': [], 'Metric_count': [], 'Metric_amount': []}
for i in map_state_list:
    p_i = path3 + i + "/"
    Agg_yrs = os.listdir(p_i)
    for j in Agg_yrs:
        p_j = p_i + j + "/"
        Agg_yrs_list = os.listdir(p_j)
        for k in Agg_yrs_list:
            p_k = p_j + k
            with open(p_k, 'r') as f:
                data = json.load(f)
                clm['district'].append(data['data']['hoverDataList'][0]['name'])
                clm['State'].append(i)
                clm['Quarter'].append(j)
                clm['Year'].append(int(k.strip('.json')))
                for metric in data['data']['hoverDataList'][0]['metric']:
                    clm['Metric_type'].append(metric['type'])
                    clm['Metric_count'].append(metric['count'])
                    clm['Metric_amount'].append(metric['amount'])

df3 = pd.DataFrame(clm)



In [16]:
df3.isnull().sum()

State            0
district         0
Year             0
Quarter          0
Metric_type      0
Metric_count     0
Metric_amount    0
dtype: int64

In [17]:
conn = sqlite3.connect("Map_Transaction_india.db")
s = conn.cursor()

In [18]:
#Create a table in database
s.execute('''CREATE TABLE IF NOT EXISTS Map_Transaction_india(
            State TEXT,
            district TEXT,
            Year TEXT,
            Quarter TEXT,
            Metric_type TEXT,
            Metric_count TEXT,
            Metric_amount TEXT
            )''')

In [19]:
s.executemany('INSERT INTO Map_Transaction_india VALUES(?,?,?,?,?,?,?)',
             zip(clm['State'],clm['district'],clm['Year'],clm['Quarter'],clm['Metric_type'],clm['Metric_count'],clm['Metric_amount']))


In [20]:
conn = sqlite3.connect('Map_Transaction_india.db')
c = conn.cursor()

In [ ]:
c.execute("SELECT * FROM Map_Transaction_india")

# Fetch all the rows in the result set
rows = s.fetchall()

# Loop through each row and print the data
for row in rows:
    print(row)

conn.commit()
# Close the connection
conn.close()    

In [21]:
#This is to direct the path to get the data as states
path4 = "/content/pulse/data/map/user/hover/country/india/state/"
map_state_list = os.listdir(path4)

# This is to extract the data's to create a dataframe
clm = {'State': [], 'Year': [], 'Quarter': [], 'No of users': [], 'AppOpen':[], 'Area':[] }
for i in map_state_list:
    p_i = path4 + i + "/"
    Agg_yrs = os.listdir(p_i)
    for j in Agg_yrs:
        p_j = p_i + j + "/"
        Agg_yrs_list = os.listdir(p_j)
        for k in Agg_yrs_list:
            p_k = p_j + k
            with open(p_k, 'r') as f:
                data = json.load(f)
                clm['State'].append(i)
                clm['Year'].append(j)
                clm['Quarter'].append(int(k.strip('.json')))
                clm['No of users'].append(data['data']['hoverData'])
                clm['AppOpen'].append(None)
                clm['Area'].append(None)
df2 = pd.DataFrame(clm)

In [ ]:
df2.head()

In [ ]:
map_users = (df2[['State','Year','No of users']])

map_users

In [ ]:
for items in (df2['No of users']):
  print(items)
  for keys in items:
    print(keys)
  

In [25]:
path5 = "/content/pulse/data/top/transaction/country/india/state/"
map_state_list = os.listdir(path5)

# This is to extract the data's to create a dataframe
clm = {'State': [], 'district':[],'Year': [], 'Quarter': [], 'Metric_type': [], 'Metric_count': [], 'Metric_amount': []}
for i in map_state_list:
    p_i = path5 + i + "/"
    Agg_yrs = os.listdir(p_i)
    for j in Agg_yrs:
        p_j = p_i + j + "/"
        Agg_yrs_list = os.listdir(p_j)
        for k in Agg_yrs_list:
            p_k = p_j + k
            with open(p_k, 'r') as f:
                data = json.load(f)
                clm['district'].append(data['data']["districts"][0]['entityName'])
                clm['Metric_type'].append(data['data']["districts"][0]['metric']['type'])
                clm['Metric_count'].append(data['data']["districts"][0]['metric']['count'])
                clm['Metric_amount'].append(data['data']["districts"][0]['metric']['amount'])
                clm['State'].append(i)
                clm['Quarter'].append(j)
                clm['Year'].append(int(k.strip('.json')))

df5=pd.DataFrame(clm)                            
                    
                   

In [ ]:
path6 = "/content/pulse/data/top/user/country/india/state/"
map_state_list = os.listdir(path6)

# This is to extract the data's to create a dataframe
clm = {'State': [], 'district':[],'Year': [], 'Quarter': [], 'No of Regi_user':[]}
for i in map_state_list:
    p_i = path6 + i + "/"
    Agg_yrs = os.listdir(p_i)
    for j in Agg_yrs:
        p_j = p_i + j + "/"
        Agg_yrs_list = os.listdir(p_j)
        for k in Agg_yrs_list:
            p_k = p_j + k
            with open(p_k, 'r') as f:
                data = json.load(f)
                clm['State'].append(i)
                clm['Quarter'].append(j)
                clm['Year'].append(int(k.strip('.json')))
                clm['district'].append(data['data']['districts'][0]['name'])
                clm['No of Regi_user'].append(data['data']['districts'][0]['registeredUsers'])
df6 = pd.DataFrame(clm)

In [ ]:
#Created 6 data frames

In [ ]:
!pip install streamlit

In [ ]:
import plotly.express as px
import matplotlib.pyplot as plot
import pandas as pd
import streamlit as st
import json

In [ ]:
india_states = json.load(open("india_states.geojson",'r'))

In [ ]:
india_states['features'][0]['properties']

{'cartodb_id': 1, 'state_code': 0, 'st_nm': 'Telangana'}

In [ ]:
Agg_Transc_Ind_State.isnull().sum

In [ ]:
Agg_Transc_Ind_State = Agg_Transc_Ind_State.to_csv("Agg_Transc_Ind_State.csv")

In [ ]:
df = pd.read_csv("Agg_Transc_Ind_State.csv")

In [ ]:
df.tail()

In [ ]:
df['State'].value_counts()

In [ ]:
df['State'] = df['State'].str.title()

In [ ]:
df['State'].value_counts()

In [ ]:
#i am creating mapping between geojson and data we have 
#for the i am gonna write a loop here
#in oreder to map this id with name of this state i am going to create dict
state_id_map = {}
for feature in india_states['features']:
  feature['id'] = feature['properties']['state_code']
  state_id_map[feature['properties']['st_nm']] = feature['id']


In [ ]:
df['State'] = df['State'].replace({'Andaman-&-Nicobar-Islands':'Andaman & Nicobar Island',
                                   'Arunachal-Pradesh':'Arunachal Pradesh',
                                   'West-Bengal':'West Bengal',
                                   'Dadra-&-Nagar-Haveli-&-Daman-&-Diu':'Dadara & Nagar Havelli',
                                   'Himachal-Pradesh':'Himachal Pradesh',
                                   'Tamil-Nadu':'Tamil Nadu',
                                   'Madhya-Pradesh':'Madhya Pradesh',
                                   'Delhi':'NCT of Delhi',
                                   'Uttar-Pradesh':'Uttar Pradesh',
                                   'Jammu-&-Kashmir':'Jammu & Kashmir',
                                   'Andhra-Pradesh':'Andhra Pradesh',
                                   'Ladakh':'Jammu & Kashmir',
                                   'Arunachal Pradesh':'Arunanchal Pradesh',
                                   'Nct Of Delhi':'NCT of Delhi'})

In [ ]:
state_id_map

In [ ]:
new_dict = dict((k.lower(), v) for k, v in state_id_map.items()) 



In [ ]:
import plotly.io as pio
pio.renderers.default= 'colab'

In [ ]:
fig=px.choropleth(df, locations='id', geojson=india_states, color = 'Transacion_count',scope='asia')

fig.update_geos(fitbounds="locations",visible=False)
fig.show()


In [ ]:
dfAg.head()

In [ ]:
dfAg['State'] = dfAg['State'].str.title()

In [ ]:
dfAg['State']

100     Andaman-&-Nicobar-Islands
101     Andaman-&-Nicobar-Islands
102     Andaman-&-Nicobar-Islands
103     Andaman-&-Nicobar-Islands
104     Andaman-&-Nicobar-Islands
                  ...            
3589                        Bihar
3590                        Bihar
3591                        Bihar
3592                        Bihar
3593                        Bihar
Name: State, Length: 3494, dtype: object

In [ ]:
dfAg['State'] = dfAg['State'].replace({'Andaman-&-Nicobar-Islands':'Andaman & Nicobar Island',
                                   'Arunachal-Pradesh':'Arunachal Pradesh',
                                   'West-Bengal':'West Bengal',
                                   'Dadra-&-Nagar-Haveli-&-Daman-&-Diu':'Dadara & Nagar Havelli',
                                   'Himachal-Pradesh':'Himachal Pradesh',
                                   'Tamil-Nadu':'Tamil Nadu',
                                   'Madhya-Pradesh':'Madhya Pradesh',
                                   'Delhi':'NCT of Delhi',
                                   'Uttar-Pradesh':'Uttar Pradesh',
                                   'Jammu-&-Kashmir':'Jammu & Kashmir',
                                   'Andhra-Pradesh':'Andhra Pradesh',
                                   'Ladakh':'Jammu & Kashmir',
                                   'Arunachal Pradesh':'Arunanchal Pradesh',
                                   'Nct Of Delhi':'NCT of Delhi',
                                   'andaman-&-nicobar-islands':'Andaman & Nicobar Island',
                                   'Andaman & Nicobar Island':'Andaman & Nicobar Island'})

In [ ]:
india_states1= json.load(open("states_india.geojson","r"))
state_id_map1 = {}
for feature in india_states['features']:
        feature['id']=feature['properties']['state_code']
        state_id_map1[feature['properties']['st_nm']]=feature['id']

new_dict = dict((k.lower(), v) for k, v in state_id_map.items()) 

dfAg['id']=dfAg['State'].apply(lambda x: new_dict[x])

fig=px.choropleth(dfAg,
                  locations='id',
                  geojson=india_states,
                  color='count',
                  hover_name='state_name',
                  hover_data=['amount'],
                  title='Transactions')
                   
                    
fig.update_geos(fitbounds='locations',visible=False)

    
    